In [6]:
from utils import mongo
import pandas as pd
import urllib.request, json
from tqdm import tqdm
import pprint
import numpy as np
import subprocess

import psycopg2
from psycopg2 import sql


In [2]:
def get_dict_from_web_json(article_id):
    """this function downloads a json file from the web and returns a dict"""
    with urllib.request.urlopen("https://www.ncbi.nlm.nih.gov/research/bionlp/RESTful/pmcoa.cgi/BioC_json/"+article_id+"/unicode") as url:
        data = json.loads(url.read().decode())
        return data

In [4]:
pmc_ids = ['PMC10047700','PMC10054737','PMC10087035','PMC10213353','PMC10226267'
,'PMC10263344','PMC10277951','PMC10310558','PMC10354928','PMC10359376'
,'PMC10364759','PMC10407498','PMC10416696','PMC10476123','PMC10626330'
,'PMC3432121','PMC4369843','PMC5209428','PMC5355508','PMC5542784'
,'PMC5579173','PMC5715046','PMC5808712','PMC5863981','PMC5900725'
,'PMC5990567','PMC6129039','PMC6257430','PMC6291156','PMC6296520'
,'PMC6331738','PMC6354192','PMC6394086','PMC6430759','PMC6433422'
,'PMC6449949','PMC6513788','PMC6795629','PMC6992684','PMC6997159'
,'PMC7103177','PMC7153184','PMC7199605','PMC7212129','PMC7227310'
,'PMC7320065','PMC7336323','PMC7397345','PMC7439541','PMC7457655'
,'PMC7489661','PMC7519527','PMC7528523','PMC7535676','PMC7539400'
,'PMC7580259','PMC7667929','PMC7765607','PMC7797855','PMC7801633'
,'PMC7814645','PMC7898229','PMC8126803','PMC8183725','PMC8208906'
,'PMC8229046','PMC8246753','PMC8346442','PMC8390156','PMC8476360'
,'PMC8489786','PMC8523496','PMC8683256','PMC8700187','PMC8724192'
,'PMC8758650','PMC8790330','PMC8793212','PMC8831416','PMC8840033'
,'PMC8863852','PMC8869881','PMC8887088','PMC9116683','PMC9161645'
,'PMC9199482','PMC9260864','PMC9262798','PMC9262801','PMC9276443'
,'PMC9300066','PMC9389786','PMC9423657','PMC9502513','PMC9523838'
,'PMC9541253','PMC9600250','PMC9635981','PMC9663802','PMC9891862'
,'PMC9909109']

In [5]:
article = get_dict_from_web_json(pmc_ids[0])

In [6]:
def get_title(article):
    return [x["text"] for x in article["documents"][0]["passages"] if x["infons"]["section_type"] == "TITLE"][0]

def remove_non_ascii(s: str) -> str:
    return "".join(c for c in s if ord(c) < 128)

def get_abstract(article):
    try:
        return [remove_non_ascii(x["text"]) for x in article["documents"][0]["passages"] if x["infons"]["type"] == "abstract"][0]
    except:
        return ""
    
def get_text(article):
    return ("".join([remove_non_ascii(x["text"]) for x in article["documents"][0]["passages"] if x["infons"]["type"] == "paragraph"]))

(get_title(article), get_abstract(article), get_text(article))

('Predictive Factors for Anastomotic Leakage Following Colorectal Cancer Surgery: Where Are We and Where Are We Going?',
 'Anastomotic leakage (AL) remains one of the most severe complications following colorectal cancer (CRC) surgery. Indeed, leaks that may occur after any type of intestinal anastomosis are commonly associated with a higher reoperation rate and an increased risk of postoperative morbidity and mortality. At first, our review aims to identify specific preoperative, intraoperative and perioperative factors that eventually lead to the development of anastomotic dehiscence based on the current literature. We will also investigate the role of several biomarkers in predicting the presence of ALs following colorectal surgery. Despite significant improvements in perioperative care, advances in surgical techniques, and a high index of suspicion of this complication, the incidence of AL remained stable during the last decades. Thus, gaining a better knowledge of the risk factors

In [58]:
text = get_text(article)

In [7]:
conn = psycopg2.connect(database="postgres", user='postgres', password='example', host='127.0.0.1', port= '5432')
conn.autocommit = True
cursor = conn.cursor()
sql = '''CREATE database leaks''';
cursor.execute(sql)

print("Database created successfully.")

DuplicateDatabase: database "leaks" already exists


In [9]:
conn = psycopg2.connect(database="leaks", user='postgres', password='example', host='127.0.0.1', port='5432')
cursor = conn.cursor()

# Drop the existing table and create a new one
cursor.execute("DROP TABLE IF EXISTS texts;")
cursor.execute("CREATE TABLE texts (id serial PRIMARY KEY, pmid varchar, title varchar, abstract varchar, text varchar);")

conn.commit()
conn.close()

In [15]:
conn = psycopg2.connect(database="leaks", user='postgres', password='example', host='127.0.0.1', port='5432')
cursor = conn.cursor()

cursor.execute("SELECT * FROM texts LIMIT 10;")
result = cursor.fetchall()
print(result)

conn.close()

[(1, 'PMC10047700', 'Predictive Factors for Anastomotic Leakage Following Colorectal Cancer Surgery: Where Are We and Where Are We Going?', 'Anastomotic leakage (AL) remains one of the most severe complications following colorectal cancer (CRC) surgery. Indeed, leaks that may occur after any type of intestinal anastomosis are commonly associated with a higher reoperation rate and an increased risk of postoperative morbidity and mortality. At first, our review aims to identify specific preoperative, intraoperative and perioperative factors that eventually lead to the development of anastomotic dehiscence based on the current literature. We will also investigate the role of several biomarkers in predicting the presence of ALs following colorectal surgery. Despite significant improvements in perioperative care, advances in surgical techniques, and a high index of suspicion of this complication, the incidence of AL remained stable during the last decades. Thus, gaining a better knowledge o

In [12]:
conn = psycopg2.connect(database="leaks", user='postgres', password='example', host='127.0.0.1', port='5432')
cursor = conn.cursor()

# Drop the existing table and create a new one
# cursor.execute("DROP TABLE IF EXISTS texts;")
# cursor.execute("CREATE TABLE texts (id serial PRIMARY KEY, pmid varchar, title varchar, abstract varchar, text varchar);")

# Iterate over the first 10 articles
for i in tqdm(range(len(pmc_ids))):
    pmc_id = pmc_ids[i]
    try:
        article = get_dict_from_web_json(str(pmc_id))
    except:
        print("error with pmid: ", pmc_id)
        continue
    title = get_title(article)
    abstract = get_abstract(article)
    text = get_text(article)

    # Insert the data into the table
    cursor.execute("INSERT INTO texts (pmid, title, abstract, text) VALUES (%s, %s, %s, %s)",
                   (pmc_id, title, abstract, abstract + " " + text))
    
    # save abstract + " " + text to a file with name pmid.txt
    with open("data/" + str(pmc_id) + ".txt", "w") as f:
        f.write(abstract + " " + text)

# Commit the changes
conn.commit()

# Retrieve and print the data from the table
cursor.execute("SELECT * FROM texts;")
result = cursor.fetchall()
print(result)

# Close the connection
conn.close()

100%|██████████| 101/101 [01:53<00:00,  1.12s/it]

[(1, 'PMC10047700', 'Predictive Factors for Anastomotic Leakage Following Colorectal Cancer Surgery: Where Are We and Where Are We Going?', 'Anastomotic leakage (AL) remains one of the most severe complications following colorectal cancer (CRC) surgery. Indeed, leaks that may occur after any type of intestinal anastomosis are commonly associated with a higher reoperation rate and an increased risk of postoperative morbidity and mortality. At first, our review aims to identify specific preoperative, intraoperative and perioperative factors that eventually lead to the development of anastomotic dehiscence based on the current literature. We will also investigate the role of several biomarkers in predicting the presence of ALs following colorectal surgery. Despite significant improvements in perioperative care, advances in surgical techniques, and a high index of suspicion of this complication, the incidence of AL remained stable during the last decades. Thus, gaining a better knowledge o

In [ ]:
# start metamap server
subprocess.Popen(["/Users/moritzduck/workspaces/metamap-mac/public_mm/bin/skrmedpostctl", "start"])
subprocess.Popen(["/Users/moritzduck/workspaces/metamap-mac/public_mm/bin/wsdserverctl", "start"])

In [ ]:

import os
import subprocess

for file in tqdm(os.listdir("data")):
    if file.endswith(".txt"):
        # append line break to file
        with open("data/" + file, "a") as f:
            f.write("\n")

        try:
            command = '/Users/moritzduck/workspaces/metamap-mac/public_mm/bin/metamap --silent --JSONf 2 -V USAbase {file} {output}'.format(file="data/" + file, output="data/" + file.replace(".txt", ".json"))
            output = subprocess.check_output(command, shell=True)
        except:
            continue

        

In [7]:
def process_json_output(data):
    entities = []
    for utt in data["AllDocuments"][0]["Document"]["Utterances"]:
        for phrase in utt["Phrases"]:
            for mapping in phrase["Mappings"]:
                for candidate in mapping["MappingCandidates"]:
               
                    startpos = int(candidate["ConceptPIs"][0]["StartPos"])
                    length = int(candidate["ConceptPIs"][0]["Length"])
                    
                    mapping_start = startpos
                    mapping_end = mapping_start + length
                
                    cui = candidate["CandidateCUI"]
                    semtype = candidate["SemTypes"][0]
                    score = candidate["CandidateScore"]
                    
                    candidate_matched = candidate["CandidateMatched"]
                    preferred = candidate["CandidatePreferred"]
                    matched = candidate["MatchedWords"]

                    entities.append((candidate_matched, score, cui, semtype, mapping_start, mapping_end))
    return entities
         

In [8]:
from tqdm import tqdm
import os
conn = psycopg2.connect(database="leaks", user='postgres', password='example', host='127.0.0.1', port='5432')

cursor = conn.cursor()
cursor.execute("CREATE INDEX pmid_index ON texts (pmid);")
cursor.execute("DROP TABLE IF EXISTS entities;")

cursor.execute(
"""CREATE TABLE IF NOT EXISTS entities (
id serial PRIMARY KEY, 
fktext INT, 
candidate varchar, 
score int, 
cui varchar, 
semtype varchar, 
start int, 
"end" int,
CONSTRAINT fk_text
    FOREIGN KEY(fktext) 
    REFERENCES texts(id)
    ON DELETE CASCADE
);
""")

# iterate over all files in the data folder and process them

for filename in tqdm(os.listdir("data")):
    if filename.endswith(".json"):
        pmid = filename.split(".")[0]

        # find the text id in the database
        cursor.execute("SELECT id FROM texts WHERE pmid = %s", (pmid,))

        result = cursor.fetchone()
        if result is not None:
            text_id = result[0]
        else:
            print("pmid not found in database: " + pmid)
            continue

        with open("data/" + filename, "r") as file:
            data = json.load(file)
        entities = process_json_output(data)
        for entity in entities:
            cursor.execute('INSERT INTO entities (fktext, candidate, score, cui, semtype, start, "end") VALUES (%s, %s, %s, %s, %s, %s, %s)',
                           (text_id, entity[0], entity[1], entity[2], entity[3], entity[4], entity[5]))

    else:
        continue


conn.commit()

100%|██████████| 166/166 [03:33<00:00,  1.29s/it]


In [19]:
conn = psycopg2.connect(database="leaks", user='postgres', password='example', host='127.0.0.1', port='5432')
cursor = conn.cursor()

cursor.execute("SELECT DISTINCT fktext FROM entities")
result = cursor.fetchall()
texts_with_entities = [x[0] for x in result]

cursor.execute("SELECT DISTINCT id FROM texts")
result = cursor.fetchall()
texts = [x[0] for x in result]

print(texts)

conn.close()

[55, 27, 23, 56, 91, 58, 8, 87, 74, 54, 29, 71, 68, 4, 34, 51, 96, 80, 70, 52, 83, 67, 63, 90, 10, 35, 45, 6, 86, 84, 39, 92, 101, 93, 89, 69, 36, 31, 50, 60, 97, 14, 66, 22, 59, 13, 65, 2, 16, 62, 75, 98, 73, 44, 11, 99, 42, 88, 82, 41, 46, 40, 43, 53, 32, 9, 7, 100, 38, 15, 79, 48, 26, 12, 85, 72, 95, 78, 57, 24, 81, 61, 19, 77, 25, 94, 30, 21, 49, 47, 3, 17, 37, 28, 20, 33, 1, 76, 5, 18, 64]


In [23]:
# get all texts that have no entities
text_ids_without_entities = list(set(texts) - set(texts_with_entities))
len(text_ids_without_entities)

# delete all texts that have no entities
conn = psycopg2.connect(database="leaks", user='postgres', password='example', host='127.0.0.1', port='5432')
cursor = conn.cursor()

for text_id in tqdm(text_ids_without_entities):
    cursor.execute("DELETE FROM texts WHERE id = %s", (text_id,))
    
conn.commit()
conn.close()


100%|██████████| 35/35 [00:00<00:00, 45.23it/s]


In [13]:
df_all = pd.DataFrame(columns=["candidate", "score", "cui", "semtype", "start", "end", "pmid"])

for i in tqdm(range(100)):
    pmid = articles[i]
    try:
        with open("data/" + str(pmid) + ".json", "r") as file:
            data = json.load(file)
    except:
        continue
    entities = process_json_output(data)
    df = pd.DataFrame(entities, columns=["candidate", "score", "cui", "semtype", "start", "end"])
    df["pmid"] = pmid

    df_all = pd.concat([df_all, df])